In [1]:
import gym
import numpy as np

#
# Environment
#
env = gym.make('CartPole-v1')
state = env.reset()
action = env.action_space.sample()

print('State space: ', env.observation_space)
print('Initial state: ', state)
print('\nAction space: ', env.action_space)
print('Random action: ', action)

State space:  Box([-4.8000002e+00 -3.4028235e+38 -4.1887903e-01 -3.4028235e+38], [4.8000002e+00 3.4028235e+38 4.1887903e-01 3.4028235e+38], (4,), float32)
Initial state:  [ 0.03574043 -0.04664144  0.02296554 -0.03243444]

Action space:  Discrete(2)
Random action:  1


In [2]:
# DQN Modeling
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense

num_state = env.observation_space.shape[0]
num_action = env.action_space.n

model = Sequential()
model.add(Dense(24, input_dim= num_state, activation='relu'))
model.add(Dense(24, activation='relu'))
model.add(Dense(num_action, activation='linear'))
model.compile(loss='mse', optimizer="adam")


/home/mash/Projects/mash-ML/venv/lib/python3.10/site-packages/tensorflow/__init__.py:29: DeprecationWarning: The distutils package is deprecated and slated for removal in Python 3.12. Use setuptools or check PEP 632 for potential alternatives
  import distutils as _distutils
2022-06-03 23:00:17.651080: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-06-03 23:00:17.651107: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/mash/Projects/mash-ML/venv/lib/python3.10/site-packages/flatbuffers/compat.py:19: DeprecationWarning: the imp module is deprecated in favour of importlib and slated for removal in Python 3.12; see the module's documentation for alternative uses
  import imp
/home/mash/Projects/mash-ML/venv/lib/python3.10/site-packages/keras/util

In [11]:
import random
from collections import deque
from tqdm import tqdm

num_episode = 1000
memory = deque(maxlen=2000)

# Hyper parameter
epsilon = 0.3
gamma = 0.95
batch_size = 32

# DQN Learning
for episode in tqdm(range(num_episode)):
    state = env.reset()
    done = False
    while not done:
        if np.random.uniform() < epsilon:
            action = env.action_space.sample()
        else:
            q_value = model.predict(state.reshape(1, num_state))
            action = np.argmax(q_value[0])
        next_state, reward, done, info = env.step(action)
        # Memory
        memory.append((state, action, reward, next_state, done))
        
        state = next_state
    
    # Replay
    if len(memory) > batch_size:
        mini_batch = random.sample(memory, batch_size)
        for state, action, reward, next_state, done in mini_batch:
            if done:
                target = reward
            else:
                target = reward + gamma * (np.max(model.predict(next_state.reshape(1, num_state))[0]))
            q_value = model.predict(state.reshape(1, num_state))
            q_value[0][action] = target
            model.fit(state.reshape(1, num_state), q_value, epochs=1, verbose=0)

env.close()

  0%|          | 0/1000 [00:00<?, ?it/s]

1/1 [==============================] - 0s 11ms/step


  0%|          | 1/1000 [00:00<03:44,  4.46it/s]

1/1 [==============================] - 0s 10ms/step


  0%|          | 2/1000 [00:00<04:35,  3.63it/s]

...

100%|█████████▉| 998/1000 [1:21:40<00:10,  5.40s/it]

1/1 [==============================] - 0s 14ms/step


100%|█████████▉| 999/1000 [1:21:46<00:05,  5.47s/it]

1/1 [==============================] - 0s 13ms/step


100%|██████████| 1000/1000 [1:21:50<00:00,  4.91s/it]


In [7]:
import os

save_dir = os.getcwd()
model_name = 'keras_dqn_trained_model.h5'

# Save model and weights
model_path = os.path.join(save_dir, model_name)
model.save(model_path)


# https://github.com/skettee/notebooks/blob/master/deep_q_network.ipynb

In [10]:
import gym
from gym.wrappers import Monitor

import base64
from IPython.display import HTML
from IPython import display as ipythondisplay

from pyvirtualdisplay import Display
display = Display(visible=0, size=(1400, 900))
display.start()

def show_video(file_infix):
    with open('./video/openaigym.video.%s.video000000.mp4' % file_infix, 'r+b') as f:
        video = f.read()
        encoded = base64.b64encode(video)
        ipythondisplay.display(HTML(data='''<video alt="Trained CartPole" autoplay 
                loop style="height: 200px;">
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
                 </video>'''.format(encoded.decode('ascii'))))
    
def wrap_env(env):
    env = Monitor(env, './video', force=True)
    return env

ImportError: cannot import name 'Monitor' from 'gym.wrappers' (/home/mash/Projects/mash-ML/venv/lib/python3.10/site-packages/gym/wrappers/__init__.py)